# Reading Data - JSON Files

**Technical Accomplishments:**
- Read data from:
  * JSON without a Schema
  * JSON with a Schema

##![Spark Logo Tiny](https://files.training.databricks.com/images/105/logo_spark_tiny.png) Getting Started

Run the following cell to configure our "classroom."

In [0]:
%run "./Includes/Classroom-Setup"

Initialized classroom variables & functions...

Datasets are already mounted to /mnt/training from wasbs://training@dbtrainwesteurope.blob.core.windows.net/

Created user-specific database

Using the database saifahmed_k_outlook_com_db .

All done!

In [0]:
%run "./Includes/Utility-Methods"

Declared various utility methods: 
 Declared printRecordsPerPartition( df:DataFrame ) for diagnostics 
 Declared computeFileStats( path:String ) returns (count:Long, bytes:Long) for diagnostics 
 Declared tracker for benchmarking 
 Declared cacheAs( df:DataFrame, name:String, level:StorageLevel ) for better debugging 
 Declared benchmarkCount( lambda:DataFrame ) returns (df:DataFrame, total:Long, duration:Long) for diagnostics 
 Declared untilStreamIsReady( name:String ) to control workflow 
 
 All done!

##![Spark Logo Tiny](https://files.training.databricks.com/images/105/logo_spark_tiny.png) Reading from JSON w/ InferSchema

Reading in JSON isn't that much different than reading in CSV files.

Let's start with taking a look at all the different options that go along with reading in JSON files.

### JSON Lines

Much like the CSV reader, the JSON reader also assumes...
* That there is one JSON object per line and...
* That it's delineated by a new-line.

This format is referred to as **JSON Lines** or **newline-delimited JSON** 

More information about this format can be found at <a href="http://jsonlines.org/" target="_blank">http://jsonlines.org</a>.

** *Note:* ** *Spark 2.2 was released on July 11th 2016. With that comes File IO improvements for CSV & JSON, but more importantly, **Support for parsing multi-line JSON and CSV files**. You can read more about that (and other features in Spark 2.2) in the <a href="https://databricks.com/blog/2017/07/11/introducing-apache-spark-2-2.html" target="_blank">Databricks Blog</a>.*

### The Data Source
* For this exercise, we will be using the file called **snapshot-2016-05-26.json** (<a href="https://wikitech.wikimedia.org/wiki/Stream.wikimedia.org/rc" target="_blank">4 MB</a> file from Wikipedia).
* The data represents a set of edits to Wikipedia articles captured in May of 2016.
* It's located on the DBFS at **dbfs:/mnt/training/wikipedia/edits/snapshot-2016-05-26.json**
* Like we did with the CSV file, we can use **&percnt;fs ls ...** to view the file on the DBFS.

In [0]:
%fs ls dbfs:/databricks-datasets/wikipedia-datasets/data-001/clickstream/raw-uncompressed-json/2015_2_clickstream.json

path name size dbfs:/databricks-datasets/wikipedia-datasets/data-001/clickstream/raw-uncompressed-json/2015_2_clickstream.json 2015_2_clickstream.json 2815233011

In [0]:
# %fs ls dbfs:/mnt/training/wikipedia/edits/snapshot-2016-05-26.json


Like we did with the CSV file, we can use **&percnt;fs head ...** to peek at the first couple lines of the JSON file.

In [0]:
%fs head dbfs:/databricks-datasets/wikipedia-datasets/data-001/clickstream/raw-uncompressed-json/2015_2_clickstream.json

[Truncated to first 65536 bytes]
{"curr_id":"3632887","n":"121","prev_title":"other-google","curr_title":"!!","type":"other"}
{"curr_id":"3632887","n":"93","prev_title":"other-wikipedia","curr_title":"!!","type":"other"}
{"curr_id":"3632887","n":"46","prev_title":"other-empty","curr_title":"!!","type":"other"}
{"curr_id":"3632887","n":"10","prev_title":"other-other","curr_title":"!!","type":"other"}
{"prev_id":"64486","curr_id":"3632887","n":"11","prev_title":"!_(disambiguation)","curr_title":"!!","type":"other"}
{"prev_id":"2061699","curr_id":"2556962","n":"19","prev_title":"Louden_Up_Now","curr_title":"!!!_(album)","type":"link"}
{"curr_id":"2556962","n":"25","prev_title":"other-empty","curr_title":"!!!_(album)","type":"other"}
{"curr_id":"2556962","n":"16","prev_title":"other-google","curr_title":"!!!_(album)","type":"other"}
{"curr_id":"2556962","n":"44","prev_title":"other-wikipedia","curr_title":"!!!_(album)","type":"other"}
{"prev_id":"64486","curr_id":"2556962","n":"15","prev_title":"!_(disambiguation)","curr_title":"!!!_(album)","type":"link"}
{"prev_id":"600744","curr_id":"2556962","n":"297","prev_title":"!!!","curr_title":"!!!_(album)","type":"link"}
{"curr_id":"6893310","n":"11","prev_title":"other-empty","curr_title":"!Hero_(album)","type":"other"}
{"prev_id":"1921683","curr_id":"6893310","n":"26","prev_title":"!Hero","curr_title":"!Hero_(album)","type":"link"}
{"curr_id":"6893310","n":"16","prev_title":"other-wikipedia","curr_title":"!Hero_(album)","type":"other"}
{"curr_id":"6893310","n":"23","prev_title":"other-google","curr_title":"!Hero_(album)","type":"other"}
{"prev_id":"8127304","curr_id":"22602473","n":"16","prev_title":"Jericho_Rosales","curr_title":"!Oka_Tokat","type":"link"}
{"prev_id":"35978874","curr_id":"22602473","n":"20","prev_title":"List_of_telenovelas_of_ABS-CBN","curr_title":"!Oka_Tokat","type":"link"}
{"curr_id":"22602473","n":"57","prev_title":"other-google","curr_title":"!Oka_Tokat","type":"other"}
{"curr_id":"22602473","n":"12","prev_title":"other-wikipedia","curr_title":"!Oka_Tokat","type":"other"}
{"curr_id":"22602473","n":"23","prev_title":"other-empty","curr_title":"!Oka_Tokat","type":"other"}
{"prev_id":"7360687","curr_id":"22602473","n":"10","prev_title":"Rica_Peralejo","curr_title":"!Oka_Tokat","type":"link"}
{"prev_id":"37104582","curr_id":"22602473","n":"11","prev_title":"Jeepney_TV","curr_title":"!Oka_Tokat","type":"link"}
{"prev_id":"34376590","curr_id":"22602473","n":"22","prev_title":"Oka_Tokat_(2012_TV_series)","curr_title":"!Oka_Tokat","type":"link"}
{"curr_id":"6810768","n":"20","prev_title":"other-wikipedia","curr_title":"!T.O.O.H.!","type":"other"}
{"curr_id":"6810768","n":"81","prev_title":"other-google","curr_title":"!T.O.O.H.!","type":"other"}
{"prev_id":"31976181","curr_id":"6810768","n":"51","prev_title":"List_of_death_metal_bands,_!–K","curr_title":"!T.O.O.H.!","type":"link"}
{"curr_id":"6810768","n":"35","prev_title":"other-empty","curr_title":"!T.O.O.H.!","type":"other"}
{"curr_id":"3243047","n":"21","prev_title":"other-empty","curr_title":"!_(album)","type":"other"}
{"prev_id":"1337475","curr_id":"3243047","n":"208","prev_title":"The_Dismemberment_Plan","curr_title":"!_(album)","type":"link"}
{"prev_id":"3284285","curr_id":"3243047","n":"78","prev_title":"The_Dismemberment_Plan_Is_Terrified","curr_title":"!_(album)","type":"link"}
{"curr_id":"3243047","n":"28","prev_title":"other-wikipedia","curr_title":"!_(album)","type":"other"}
{"prev_id":"2098292","curr_id":"899480","n":"58","prev_title":"United_States_military_award_devices","curr_title":"\"A\"_Device","type":"link"}
{"prev_id":"194844","curr_id":"899480","n":"15","prev_title":"USS_Yorktown_(CV-5)","curr_title":"\"A\"_Device","type":"link"}
{"curr_id":"899480","n":"17","prev_title":"other-google","curr_title":"\"A\"_Device","type":"other"}
{"curr_id":"899480","n":"13","prev_title":"other-empty","curr_title":"\"A\"_Device","type":"other"}
{"curr_id":"899480","n":"29","prev_title":"other-wikipedia","curr_title

### Read The JSON File

The command to read in JSON looks very similar to that of CSV.

In addition to reading the JSON file, we will also print the resulting schema.

In [0]:
jsonFile = "dbfs:/databricks-datasets/wikipedia-datasets/data-001/clickstream/raw-uncompressed-json/2015_2_clickstream.json"

wikiEditsDF = (spark.read           # The DataFrameReader
    .option("inferSchema", "true")  # Automatically infer data types & column names
    .json(jsonFile)                 # Creates a DataFrame from JSON after reading in the file
 )
wikiEditsDF.printSchema()

root
-- curr_id: string (nullable = true)
-- curr_title: string (nullable = true)
-- n: string (nullable = true)
-- prev_id: string (nullable = true)
-- prev_title: string (nullable = true)
-- type: string (nullable = true)


With our DataFrame created, we can now take a peak at the data.

But to demonstrate a unique aspect of JSON data (or any data with embedded fields), we will first create a temporary view and then view the data via SQL:

In [0]:
# create a view called wiki_edits
wikiEditsDF.createOrReplaceTempView("wiki_edits")

And now we can take a peak at the data with simple SQL SELECT statement:

In [0]:
%sql

SELECT * FROM wiki_edits 

curr_id curr_title n prev_id prev_title type 3632887 !! 121 null other-google other 3632887 !! 93 null other-wikipedia other 3632887 !! 46 null other-empty other 3632887 !! 10 null other-other other 3632887 !! 11 64486 !_(disambiguation) other 2556962 !!!_(album) 19 2061699 Louden_Up_Now link 2556962 !!!_(album) 25 null other-empty other 2556962 !!!_(album) 16 null other-google other 2556962 !!!_(album) 44 null other-wikipedia other 2556962 !!!_(album) 15 64486 !_(disambiguation) link 2556962 !!!_(album) 297 600744 !!! link 6893310 !Hero_(album) 11 null other-empty other 6893310 !Hero_(album) 26 1921683 !Hero link 6893310 !Hero_(album) 16 null other-wikipedia other 6893310 !Hero_(album) 23 null other-google other 22602473 !Oka_Tokat 16 8127304 Jericho_Rosales link 22602473 !Oka_Tokat 20 35978874 List_of_telenovelas_of_ABS-CBN link 22602473 !Oka_Tokat 57 null other-google other 22602473 !Oka_Tokat 12 null other-wikipedia other 22602473 !Oka_Tokat 23 null other-empty other 22602473 !Oka_Tokat 10 7360687 Rica_Peralejo link 22602473 !Oka_Tokat 11 37104582 Jeepney_TV link 22602473 !Oka_Tokat 22 34376590 Oka_Tokat_(2012_TV_series) link 6810768 !T.O.O.H.! 20 null other-wikipedia other 6810768 !T.O.O.H.! 81 null other-google other 6810768 !T.O.O.H.! 51 31976181 List_of_death_metal_bands,_!–K link 6810768 !T.O.O.H.! 35 null other-empty other 3243047 !_(album) 21 null other-empty other 3243047 !_(album) 208 1337475 The_Dismemberment_Plan link 3243047 !_(album) 78 3284285 The_Dismemberment_Plan_Is_Terrified link 3243047 !_(album) 28 null other-wikipedia other 899480 "A"_Device 58 2098292 United_States_military_award_devices link 899480 "A"_Device 15 194844 USS_Yorktown_(CV-5) link 899480 "A"_Device 17 null other-google other 899480 "A"_Device 13 null other-empty other 899480 "A"_Device 29 null other-wikipedia other 899480 "A"_Device 11 878246 American_Defense_Service_Medal link 899480 "A"_Device 24 855901 Overseas_Service_Ribbon other 899480 "A"_Device 33 206427 USS_Ranger_(CV-4) link 899480 "A"_Device 47 773691 Antarctica_Service_Medal link 1282996 "A"_Is_for_Alibi 43 2301720 Kinsey_Millhone link 1282996 "A"_Is_for_Alibi 45 null other-empty other 1282996 "A"_Is_for_Alibi 10 null other-yahoo other 1282996 "A"_Is_for_Alibi 207 470006 Sue_Grafton link 1282996 "A"_Is_for_Alibi 18 null other-other other 1282996 "A"_Is_for_Alibi 31 null other-wikipedia other 1282996 "A"_Is_for_Alibi 272 null other-google other 1282996 "A"_Is_for_Alibi 10 39606873 "W"_Is_for_Wasted link 9003666 "And"_theory_of_conservatism 17 26181056 And link 9003666 "And"_theory_of_conservatism 109 null other-wikipedia other 9003666 "And"_theory_of_conservatism 18 null other-google other 39072529 "Bassy"_Bob_Brockmann 49 null other-google other 39072529 "Bassy"_Bob_Brockmann 10 null other-other other null "Bigfoot"_Wallace 15 11273993 Colt_1851_Navy_Revolver redlink 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 12 12571133 "V"_Is_for_Vagina link 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 24 113468 The_Mission link 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 15 14096078 Trent_Reznor_discography other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 42 null other-empty other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 15 1375614 Tapeworm_(band) other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 25 159547 Milla_Jovovich other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 73 28639397 Sound_into_Blood_into_Wine link 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 30 1893465 Carina_Round other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 10 33622887 Conditions_of_My_Parole link 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 25 147692 Tim_Alexander other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE

Notice the **geocoding** column has embedded data.

You can expand the fields by clicking the right triangle in each row.

But we can also reference the sub-fields directly as we see in the following SQL statement:

In [0]:
%sql
SELECT *
FROM wiki_edits 
WHERE prev_id IS NOT NULL

curr_id curr_title n prev_id prev_title type 3632887 !! 11 64486 !_(disambiguation) other 2556962 !!!_(album) 19 2061699 Louden_Up_Now link 2556962 !!!_(album) 15 64486 !_(disambiguation) link 2556962 !!!_(album) 297 600744 !!! link 6893310 !Hero_(album) 26 1921683 !Hero link 22602473 !Oka_Tokat 16 8127304 Jericho_Rosales link 22602473 !Oka_Tokat 20 35978874 List_of_telenovelas_of_ABS-CBN link 22602473 !Oka_Tokat 10 7360687 Rica_Peralejo link 22602473 !Oka_Tokat 11 37104582 Jeepney_TV link 22602473 !Oka_Tokat 22 34376590 Oka_Tokat_(2012_TV_series) link 6810768 !T.O.O.H.! 51 31976181 List_of_death_metal_bands,_!–K link 3243047 !_(album) 208 1337475 The_Dismemberment_Plan link 3243047 !_(album) 78 3284285 The_Dismemberment_Plan_Is_Terrified link 899480 "A"_Device 58 2098292 United_States_military_award_devices link 899480 "A"_Device 15 194844 USS_Yorktown_(CV-5) link 899480 "A"_Device 11 878246 American_Defense_Service_Medal link 899480 "A"_Device 24 855901 Overseas_Service_Ribbon other 899480 "A"_Device 33 206427 USS_Ranger_(CV-4) link 899480 "A"_Device 47 773691 Antarctica_Service_Medal link 1282996 "A"_Is_for_Alibi 43 2301720 Kinsey_Millhone link 1282996 "A"_Is_for_Alibi 207 470006 Sue_Grafton link 1282996 "A"_Is_for_Alibi 10 39606873 "W"_Is_for_Wasted link 9003666 "And"_theory_of_conservatism 17 26181056 And link null "Bigfoot"_Wallace 15 11273993 Colt_1851_Navy_Revolver redlink 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 12 12571133 "V"_Is_for_Vagina link 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 24 113468 The_Mission link 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 15 14096078 Trent_Reznor_discography other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 15 1375614 Tapeworm_(band) other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 25 159547 Milla_Jovovich other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 73 28639397 Sound_into_Blood_into_Wine link 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 30 1893465 Carina_Round other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 10 33622887 Conditions_of_My_Parole link 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 25 147692 Tim_Alexander other 25033979 "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) 593 4619790 Puscifer link null "Chúc_Mừng_Năm_Mới"_or_best_wishes_for_the_new_year. 51 69161 Tết redlink null "Cool_Hand_Conor"_O'Neill 14 1438509 List_of_Old_West_gunfighters redlink 331586 "Crocodile"_Dundee 59 489033 List_of_Academy_Awards_ceremonies link 331586 "Crocodile"_Dundee 38 10040606 List_of_Australian_films other 331586 "Crocodile"_Dundee 154 2564144 Crocodile_Dundee_in_Los_Angeles link 331586 "Crocodile"_Dundee 14 6127928 Bobby_Alto other 331586 "Crocodile"_Dundee 13 152171 Baz_Luhrmann link 331586 "Crocodile"_Dundee 348 8078282 Australia_(2008_film) link 331586 "Crocodile"_Dundee 66 37386608 2015_in_film link 331586 "Crocodile"_Dundee 12 34557 1980s other 331586 "Crocodile"_Dundee 297 1118809 "Crocodile"_Dundee_II link 331586 "Crocodile"_Dundee 52 7033 Caitlin_Clarke other 331586 "Crocodile"_Dundee 31 72766 Dundee_(disambiguation) other 331586 "Crocodile"_Dundee 221 171612 1986_in_film link 331586 "Crocodile"_Dundee 34 2376452 Australian_New_Wave other 331586 "Crocodile"_Dundee 60 1248074 David_Gulpilil link 331586 "Crocodile"_Dundee 10 865241 Crocodile_Hunter other 331586 "Crocodile"_Dundee 12 196020 Crocodilia link 331586 "Crocodile"_Dundee 85 643649 List_of_most_watched_television_broadcasts link 331586 "Crocodile"_Dundee 13 8306521 Anne_Carlisle other 331586 "Crocodile"_Dundee 18 1448969 Bart_vs._Australia other 331586 "Crocodile"_Dundee 153 70209 Cinema_of_Australia link 331586 "Crocodile"_Dundee 18 4008173 59th_Academy_Awards link 331586 "Crocodile"_Dundee 17 331460 Bowie_knife link 331586 "Crocodile"_Dundee 21 3788

### Review: Reading from JSON w/ InferSchema

While there are similarities between reading in CSV & JSON there are some key differences:
* We only need one job even when inferring the schema.
* There is no header which is why there isn't a second job in this case - the column names are extracted from the JSON object's attributes.
* Unlike CSV which reads in 100% of the data, the JSON reader only samples the data.  
**Note:** In Spark 2.2 the behavior was changed to read in the entire JSON file.

##![Spark Logo Tiny](https://files.training.databricks.com/images/105/logo_spark_tiny.png) Reading from JSON w/ User-Defined Schema

To avoid the extra job, we can (just like we did with CSV) specify the schema for the `DataFrame`.

### Step #1 - Create the Schema

Compared to our CSV example, the structure of this data is a little more complex.

Note that we can support complex data types as seen in the field `geocoding`.

In [0]:
from pyspark.sql.types import *

jsonSchema = StructType([
  StructField("curr_id", IntegerType(), True),
  StructField("curr_title", StringType(), True),
  StructField("n", IntegerType(), True),
  StructField("prev_id", IntegerType(), True),
  StructField("prev_title", StringType(), True),
  StructField("type", StringType(), True)
])

That was a lot of typing to get our schema!

For a small file, manually creating the the schema may not be worth the effort.

However, for a large file, the time to manually create the schema may be worth the trade off of a really long infer-schema process.

### Step #2 - Read in the JSON

Next, we will read in the JSON file and once again print its schema.

In [0]:
(spark.read            # The DataFrameReader
  .schema(jsonSchema)  # Use the specified schema
  .json(jsonFile)      # Creates a DataFrame from JSON after reading in the file
  .printSchema()
)

root
-- curr_id: integer (nullable = true)
-- curr_title: string (nullable = true)
-- n: integer (nullable = true)
-- prev_id: integer (nullable = true)
-- prev_title: string (nullable = true)
-- type: string (nullable = true)

### Review: Reading from JSON w/ User-Defined Schema
* Just like CSV, providing the schema avoids the extra jobs.
* The schema allows us to rename columns and specify alternate data types.
* Can get arbitrarily complex in its structure.

Let's take a look at some of the other details of the `DataFrame` we just created for comparison sake.

In [0]:
jsonDF = (spark.read
  .schema(jsonSchema)
  .json(jsonFile)    
)
print("Partitions: " + str(jsonDF.rdd.getNumPartitions()))
printRecordsPerPartition(jsonDF)
print("-"*80)

Partitions: 21
Per-Partition Counts
#1: 1,057,700
#2: 1,082,367
#3: 1,081,726
#4: 1,077,869
#5: 1,082,970
#6: 1,046,353
#7: 1,075,157
#8: 1,083,582
#9: 1,081,421
#10: 1,056,054
#11: 1,059,632
#12: 1,081,022
#13: 1,080,271
#14: 1,080,853
#15: 1,074,159
#16: 1,068,406
#17: 1,066,563
#18: 1,079,317
#19: 1,082,750
#20: 1,063,238
#21: 1,048,487
--------------------------------------------------------------------------------

And of course we can view that data here:

In [0]:
display(jsonDF)

curr_id curr_title n prev_id prev_title type null !! null null other-google other null !! null null other-wikipedia other null !! null null other-empty other null !! null null other-other other null !! null null !_(disambiguation) other null !!!_(album) null null Louden_Up_Now link null !!!_(album) null null other-empty other null !!!_(album) null null other-google other null !!!_(album) null null other-wikipedia other null !!!_(album) null null !_(disambiguation) link null !!!_(album) null null !!! link null !Hero_(album) null null other-empty other null !Hero_(album) null null !Hero link null !Hero_(album) null null other-wikipedia other null !Hero_(album) null null other-google other null !Oka_Tokat null null Jericho_Rosales link null !Oka_Tokat null null List_of_telenovelas_of_ABS-CBN link null !Oka_Tokat null null other-google other null !Oka_Tokat null null other-wikipedia other null !Oka_Tokat null null other-empty other null !Oka_Tokat null null Rica_Peralejo link null !Oka_Tokat null null Jeepney_TV link null !Oka_Tokat null null Oka_Tokat_(2012_TV_series) link null !T.O.O.H.! null null other-wikipedia other null !T.O.O.H.! null null other-google other null !T.O.O.H.! null null List_of_death_metal_bands,_!–K link null !T.O.O.H.! null null other-empty other null !_(album) null null other-empty other null !_(album) null null The_Dismemberment_Plan link null !_(album) null null The_Dismemberment_Plan_Is_Terrified link null !_(album) null null other-wikipedia other null "A"_Device null null United_States_military_award_devices link null "A"_Device null null USS_Yorktown_(CV-5) link null "A"_Device null null other-google other null "A"_Device null null other-empty other null "A"_Device null null other-wikipedia other null "A"_Device null null American_Defense_Service_Medal link null "A"_Device null null Overseas_Service_Ribbon other null "A"_Device null null USS_Ranger_(CV-4) link null "A"_Device null null Antarctica_Service_Medal link null "A"_Is_for_Alibi null null Kinsey_Millhone link null "A"_Is_for_Alibi null null other-empty other null "A"_Is_for_Alibi null null other-yahoo other null "A"_Is_for_Alibi null null Sue_Grafton link null "A"_Is_for_Alibi null null other-other other null "A"_Is_for_Alibi null null other-wikipedia other null "A"_Is_for_Alibi null null other-google other null "A"_Is_for_Alibi null null "W"_Is_for_Wasted link null "And"_theory_of_conservatism null null And link null "And"_theory_of_conservatism null null other-wikipedia other null "And"_theory_of_conservatism null null other-google other null "Bassy"_Bob_Brockmann null null other-google other null "Bassy"_Bob_Brockmann null null other-other other null "Bigfoot"_Wallace null null Colt_1851_Navy_Revolver redlink null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null "V"_Is_for_Vagina link null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null The_Mission link null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null Trent_Reznor_discography other null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null other-empty other null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null Tapeworm_(band) other null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null Milla_Jovovich other null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null Sound_into_Blood_into_Wine link null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null Carina_Round other null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null Conditions_of_My_Parole link null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null Tim_Alexander other null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null Puscifer link null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_Reference_HERE) null null other-wikipedia other null "C"_is_for_(Please_Insert_Sophomoric_Genitalia_

## Next steps

Start the next lesson, [Reading Data - Parquet]($./3.Reading%20Data%20-%20Parquet)